# Create a small subset to inspect the datasets

In [1]:
import random
import shutil
from pathlib import Path
import os

In [2]:
ROOT = Path("/dss/dsstbyfs02/pn49ci/pn49ci-dss-0022") # Root-Verzeichnis
DATA_PATH = ROOT / "data" # Verzeichnis in dem alle Datensätze gespeichert sind 
DATASET_ROOT = DATA_PATH / "xview2/test"
# Pfad zum xView2 Datensatz
IMAGE_ROOT = DATASET_ROOT / "png_images"
LABEL_ROOT = DATASET_ROOT / "targets"


SUB_DS = DATA_PATH / "xview2-subset/test" # An diesem Ort soll der Ordner für das xView 2 Subset erstellt werden
SUB_IMAGES = SUB_DS / "png_images" # auch hier werden images und 
SUB_LABEL = SUB_DS / "targets" # label getrennt

In [ ]:
#on zum Leeren eines Verzeichnisses


In [3]:
# Zielverzeichnisse erstellen
os.makedirs(SUB_IMAGES, exist_ok = True)
os.makedirs(SUB_LABEL, exist_ok = True)


Es werden je 5000 Bild Paare und Label paare heruntergeladen 

750 für validation und test

In [4]:

# Vorherige Dateien löschen
for folder in [SUB_IMAGES, SUB_LABEL]:
    if os.path.exists(folder):
        shutil.rmtree(folder)  # Löscht das gesamte Verzeichnis
    os.makedirs(folder)  # Erstellt es neu
    
# Sicherstellen, dass Zielverzeichnisse existieren
SUB_IMAGES.mkdir(parents=True, exist_ok=True)
SUB_LABEL.mkdir(parents=True, exist_ok=True)

# Alle TIF-Dateien abrufen
image_files = [file for file in os.listdir(IMAGE_ROOT) if file.endswith(".png")]

# Nur "pre"-Bilder auswählen
pre_images = [img for img in image_files if "_pre_disaster" in img]

# Zufällige Auswahl von `pre`-Bildern
sample_number = 50
selected_pre_images = random.sample(pre_images, min(sample_number, len(pre_images)))

# Kopieren der Bild-Paare und zugehörigen Labels
for pre_image in selected_pre_images:
    post_image = pre_image.replace("_pre_disaster", "_post_disaster")  # Passendes "post"-Bild finden
    pre_label = pre_image.replace(".png", ".png")  # Entsprechendes Label für pre
    post_label = post_image.replace(".png", ".png")  # Entsprechendes Label für post

    # Dateien kopieren, falls sie existieren
    for img, lbl in [(pre_image, pre_label), (post_image, post_label)]:
        img_path = IMAGE_ROOT / img
        lbl_path = LABEL_ROOT / lbl

        if img_path.exists():
            shutil.copy(img_path, SUB_IMAGES / img)

        if lbl_path.exists():
            shutil.copy(lbl_path, SUB_LABEL / lbl)

print(f"Gespeicherte {len(selected_pre_images)} Bild-Paare mit zugehörigen Labels.")

Gespeicherte 50 Bild-Paare mit zugehörigen Labels.


----------------------------------------------

This part creates the main Train and Validation folder

In [2]:
import os
import shutil
import random
from pathlib import Path
import numpy as np

# Pfade definieren
ROOT = Path("/dss/dsstbyfs02/pn49ci/pn49ci-dss-0022")  # Root-Verzeichnis
DATA_PATH = ROOT / "data"  # Verzeichnis, in dem alle Datensätze gespeichert sind 
DATASET_ROOT = DATA_PATH / "xview2/tier3"  # Pfad zum xView2 Datensatz
IMAGE_ROOT = DATASET_ROOT / "png_images"
LABEL_ROOT = DATASET_ROOT / "targets"

print(f"Quellverzeichnisse:")
print(f"- Bilder: {IMAGE_ROOT}")
print(f"- Masken: {LABEL_ROOT}")
def clear_directory(directory_path):
    if os.path.exists(directory_path):
        print(f"Leere Verzeichnis: {directory_path}")
        for file in os.listdir(directory_path):
            file_path = os.path.join(directory_path, file)
            if os.path.isfile(file_path):
                os.remove(file_path)
                print(f"  Gelöscht: {file_path}")
            elif os.path.isdir(file_path):
                shutil.rmtree(file_path)
                print(f"  Gelöscht (Unterverzeichnis): {file_path}")
        print(f"Verzeichnis {directory_path} erfolgreich geleert")
    else:
        print(f"Verzeichnis {directory_path} existiert nicht")

# Alle Zielverzeichnisse leeren, bevor neue Dateien kopiert werden
print("\n" + "="*60)
print("LEERE ZIELVERZEICHNISSE")
print("="*60)
clear_directory(TRAIN_IMAGES)
clear_directory(TRAIN_LABELS)
clear_directory(VAL_IMAGES)
clear_directory(VAL_LABELS)
# Prüfen, ob Quellverzeichnisse existieren
if not os.path.exists(IMAGE_ROOT):
    print(f"FEHLER: Bildverzeichnis {IMAGE_ROOT} existiert nicht!")
if not os.path.exists(LABEL_ROOT):
    print(f"FEHLER: Maskenverzeichnis {LABEL_ROOT} existiert nicht!")

# Zielverzeichnisse
TRAIN_DS = DATA_PATH / "xview2/train"
VAL_DS = DATA_PATH / "xview2/val"

TRAIN_IMAGES = TRAIN_DS / "png_images"
TRAIN_LABELS = TRAIN_DS / "targets"
VAL_IMAGES = VAL_DS / "png_images"
VAL_LABELS = VAL_DS / "targets"

print(f"\nZielverzeichnisse:")
print(f"- Train Bilder: {TRAIN_IMAGES}")
print(f"- Train Masken: {TRAIN_LABELS}")
print(f"- Val Bilder: {VAL_IMAGES}")
print(f"- Val Masken: {VAL_LABELS}")

# Erstellen der Zielverzeichnisse
for folder in [TRAIN_IMAGES, TRAIN_LABELS, VAL_IMAGES, VAL_LABELS]:
    os.makedirs(folder, exist_ok=True)
    print(f"Verzeichnis erstellt/geprüft: {folder}")

# Alle PNG-Dateien abrufen
image_files = [file for file in os.listdir(IMAGE_ROOT) if file.endswith(".png")]
print(f"\nGefundene PNG-Dateien: {len(image_files)}")

# Nur "pre"-Bilder auswählen, um Bildpaare zu identifizieren
pre_images = [img for img in image_files if "_pre_disaster" in img]
print(f"Davon sind {len(pre_images)} 'pre-disaster' Bilder")

# Ein paar Beispiele ausgeben
if pre_images:
    print("Beispiele für gefundene 'pre-disaster' Bilder:")
    for i in range(min(3, len(pre_images))):
        print(f"- {pre_images[i]}")
else:
    print("WARNUNG: Keine 'pre-disaster' Bilder gefunden!")

# Aufteilung festlegen (75% Train, 25% Val)
random.shuffle(pre_images)  # Mischen, um eine zufällige Verteilung zu gewährleisten
split_idx = int(len(pre_images) * 0.75)
train_pre_images = pre_images[:split_idx]
val_pre_images = pre_images[split_idx:]

print(f"\nAufteilung:")
print(f"- Train: {len(train_pre_images)} Bildpaare ({len(train_pre_images)/len(pre_images)*100:.1f}%)")
print(f"- Val: {len(val_pre_images)} Bildpaare ({len(val_pre_images)/len(pre_images)*100:.1f}%)")

# Funktion, um Bildpaare und zugehörige Masken zu kopieren
def copy_image_pairs_and_masks(pre_image_list, target_img_dir, target_mask_dir):
    copied_pairs = 0
    missing_files = 0
    
    print(f"\nStarte Kopiervorgang für {len(pre_image_list)} Bildpaare...")
    
    for i, pre_image in enumerate(pre_image_list):
        if i % 100 == 0 and i > 0:  # Status-Update alle 100 Bildpaare
            print(f"  Fortschritt: {i}/{len(pre_image_list)} Bildpaare verarbeitet...")
            
        post_image = pre_image.replace("_pre_disaster", "_post_disaster")  # Passendes "post"-Bild finden
        pre_label = pre_image  # Entsprechende Maske für pre
        post_label = post_image  # Entsprechende Maske für post
        
        all_files_exist = True
        
        # Prüfen, ob alle Dateien existieren
        for img, lbl in [(pre_image, pre_label), (post_image, post_label)]:
            img_path = IMAGE_ROOT / img
            lbl_path = LABEL_ROOT / lbl
            
            if not img_path.exists():
                print(f"FEHLER: Bilddatei {img_path} existiert nicht.")
                all_files_exist = False
                missing_files += 1
                
            if not lbl_path.exists():
                print(f"FEHLER: Maskendatei {lbl_path} existiert nicht.")
                all_files_exist = False
                missing_files += 1
        
        # Nur kopieren, wenn alle Dateien existieren
        if all_files_exist:
            # Zeige an, welche Dateien kopiert werden (nur für das erste Paar)
            if copied_pairs == 0:
                print(f"\nBeispiel für das erste kopierte Bildpaar:")
                for img, lbl in [(pre_image, pre_label), (post_image, post_label)]:
                    print(f"  Kopiere Bild: {IMAGE_ROOT / img} -> {target_img_dir / img}")
                    print(f"  Kopiere Maske: {LABEL_ROOT / lbl} -> {target_mask_dir / lbl}")
            
            # Kopieren durchführen
            for img, lbl in [(pre_image, pre_label), (post_image, post_label)]:
                img_path = IMAGE_ROOT / img
                lbl_path = LABEL_ROOT / lbl
                
                shutil.copy(img_path, target_img_dir / img)
                shutil.copy(lbl_path, target_mask_dir / lbl)
            
            copied_pairs += 1
    
    print(f"\nKopiervorgang abgeschlossen.")
    print(f"- Erfolgreich kopierte Bildpaare: {copied_pairs}")
    print(f"- Fehlende Dateien: {missing_files}")
    
    return copied_pairs

print("\n" + "="*60)
print("STARTE KOPIERVORGANG FÜR TRAIN-DATEN")
print("="*60)
# Kopieren der Train-Daten (75%)
train_pairs = copy_image_pairs_and_masks(train_pre_images, TRAIN_IMAGES, TRAIN_LABELS)

print("\n" + "="*60)
print("STARTE KOPIERVORGANG FÜR VAL-DATEN")
print("="*60)
# Kopieren der Val-Daten (25%)
val_pairs = copy_image_pairs_and_masks(val_pre_images, VAL_IMAGES, VAL_LABELS)

# Statistik ausgeben
print("\n" + "="*60)
print("ZUSAMMENFASSUNG")
print("="*60)
print(f"Ursprüngliche Anzahl an Bildpaaren: {len(pre_images)}")
print(f"Train-Split ({len(train_pre_images)/len(pre_images)*100:.1f}%): {len(train_pre_images)} Bildpaare")
print(f"Val-Split ({len(val_pre_images)/len(pre_images)*100:.1f}%): {len(val_pre_images)} Bildpaare")
print(f"Tatsächlich kopierte Bildpaare: Train = {train_pairs}, Val = {val_pairs}")

# Überprüfen, ob die erwartete Anzahl an Dateien in den Zielordnern vorhanden ist
print("\nÜberprüfung der Zielordner:")
train_img_count = len(os.listdir(TRAIN_IMAGES))
train_mask_count = len(os.listdir(TRAIN_LABELS))
val_img_count = len(os.listdir(VAL_IMAGES))
val_mask_count = len(os.listdir(VAL_LABELS))

print(f"Train Bilder: {train_img_count} (erwartet: {train_pairs*2})")
print(f"Train Masken: {train_mask_count} (erwartet: {train_pairs*2})")
print(f"Val Bilder: {val_img_count} (erwartet: {val_pairs*2})")
print(f"Val Masken: {val_mask_count} (erwartet: {val_pairs*2})")

Quellverzeichnisse:
- Bilder: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/tier3/png_images
- Masken: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/tier3/targets

LEERE ZIELVERZEICHNISSE
Leere Verzeichnis: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/portugal-wildfire_00000741_pre_disaster.png
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/pinery-bushfire_00001644_post_disaster.png
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/woolsey-fire_00000586_post_disaster.png
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/pinery-bushfire_00001417_pre_disaster.png
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/mexico-earthquake_00000037_post_disaster.png
  Gelöscht: /dss/dsstbyfs02/pn49ci/pn49ci-dss-0022/data/xview2/train/png_images/nepal-flooding_000002